In [145]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [146]:
import math
#import pandas_datareader as web
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM, Dropout, BatchNormalization, Activation
import matplotlib.pyplot as plt
import plotly.graph_objects as go
plt.style.use ('fivethirtyeight')
import plotly.express as px
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot 

# Feature Engineering et Preprocessing




In [147]:
data2 = pd.read_csv('indexData.csv')
data = data2.set_index('Date')
data

Index         Open         High          Low        Close  \
Date                                                                   
1965-12-31   NYA   528.690002   528.690002   528.690002   528.690002   
1966-01-03   NYA   527.210022   527.210022   527.210022   527.210022   
1966-01-04   NYA   527.840027   527.840027   527.840027   527.840027   
1966-01-05   NYA   531.119995   531.119995   531.119995   531.119995   
1966-01-06   NYA   532.070007   532.070007   532.070007   532.070007   
...          ...          ...          ...          ...          ...   
2021-05-27  N100  1241.119995  1251.910034  1241.119995  1247.069946   
2021-05-28  N100  1249.469971  1259.209961  1249.030029  1256.599976   
2021-05-31  N100  1256.079956  1258.880005  1248.140015  1248.930054   
2021-06-01  N100  1254.609985  1265.660034  1254.609985  1258.579956   
2021-06-02  N100  1258.489990  1263.709961  1258.239990  1263.619995   

              Adj Close       Volume  
Date                                  
1965-12-31   528.690002          0.0  
1966-01-03   527.210022          0.0  
1966-01-04   527.840027          0.0  
1966-01-05   531.119995          0.0  
1966-01-06   532.070007          0.0  
...                 ...          ...  
2021-05-27  1247.069946  379696400.0  
2021-05-28  1256.599976  160773400.0  
2021-05-31  1248.930054   91173700.0  
2021-06-01  1258.579956  155179900.0  
2021-06-02  1263.619995  148465000.0  

[112457 rows x 7 columns]

In [148]:
data.head()
data.tail(5)

Index         Open         High          Low        Close  \
Date                                                                   
2021-05-27  N100  1241.119995  1251.910034  1241.119995  1247.069946   
2021-05-28  N100  1249.469971  1259.209961  1249.030029  1256.599976   
2021-05-31  N100  1256.079956  1258.880005  1248.140015  1248.930054   
2021-06-01  N100  1254.609985  1265.660034  1254.609985  1258.579956   
2021-06-02  N100  1258.489990  1263.709961  1258.239990  1263.619995   

              Adj Close       Volume  
Date                                  
2021-05-27  1247.069946  379696400.0  
2021-05-28  1256.599976  160773400.0  
2021-05-31  1248.930054   91173700.0  
2021-06-01  1258.579956  155179900.0  
2021-06-02  1263.619995  148465000.0

In [149]:
data = data.dropna()
data.Index.unique()

array(['NYA', 'IXIC', 'HSI', '000001.SS', 'GSPTSE', '399001.SZ', 'NSEI',
       'GDAXI', 'KS11', 'SSMI', 'TWII', 'J203.JO', 'N225', 'N100'],
      dtype=object)

### Volume échangé

In [150]:
df_info = pd.read_csv("indexInfo.csv")
df_info

Region                          Exchange      Index Currency
0   United States           New York Stock Exchange        NYA      USD
1   United States                            NASDAQ       IXIC      USD
2       Hong Kong          Hong Kong Stock Exchange        HSI      HKD
3           China           Shanghai Stock Exchange  000001.SS      CNY
4           Japan              Tokyo Stock Exchange       N225      JPY
5          Europe                          Euronext       N100      EUR
6           China           Shenzhen Stock Exchange  399001.SZ      CNY
7          Canada            Toronto Stock Exchange     GSPTSE      CAD
8           India  National Stock Exchange of India       NSEI      INR
9         Germany          Frankfurt Stock Exchange      GDAXI      EUR
10          Korea                    Korea Exchange       KS11      KRW
11    Switzerland                SIX Swiss Exchange       SSMI      CHF
12         Taiwan             Taiwan Stock Exchange       TWII      TWD
13   South Africa       Johannesburg Stock Exchange    J203.JO      ZAR

In [151]:
df_merge = data2.merge(df_info, on = "Index", how = "inner" )
df_merge

Index        Date         Open         High          Low        Close  \
0        NYA  1965-12-31   528.690002   528.690002   528.690002   528.690002   
1        NYA  1966-01-03   527.210022   527.210022   527.210022   527.210022   
2        NYA  1966-01-04   527.840027   527.840027   527.840027   527.840027   
3        NYA  1966-01-05   531.119995   531.119995   531.119995   531.119995   
4        NYA  1966-01-06   532.070007   532.070007   532.070007   532.070007   
...      ...         ...          ...          ...          ...          ...   
112452  N100  2021-05-27  1241.119995  1251.910034  1241.119995  1247.069946   
112453  N100  2021-05-28  1249.469971  1259.209961  1249.030029  1256.599976   
112454  N100  2021-05-31  1256.079956  1258.880005  1248.140015  1248.930054   
112455  N100  2021-06-01  1254.609985  1265.660034  1254.609985  1258.579956   
112456  N100  2021-06-02  1258.489990  1263.709961  1258.239990  1263.619995   

          Adj Close       Volume         Region                 Exchange  \
0        528.690002          0.0  United States  New York Stock Exchange   
1        527.210022          0.0  United States  New York Stock Exchange   
2        527.840027          0.0  United States  New York Stock Exchange   
3        531.119995          0.0  United States  New York Stock Exchange   
4        532.070007          0.0  United States  New York Stock Exchange   
...             ...          ...            ...                      ...   
112452  1247.069946  379696400.0         Europe                 Euronext   
112453  1256.599976  160773400.0         Europe                 Euronext   
112454  1248.930054   91173700.0         Europe                 Euronext   
112455  1258.579956  155179900.0         Europe                 Euronext   
112456  1263.619995  148465000.0         Europe                 Euronext   

       Currency  
0           USD  
1           USD  
2           USD  
3           USD  
4           USD  
...         ...  
112452      EUR  
112453      EUR  
112454      EUR  
112455      EUR  
112456      EUR  

[112457 rows x 11 columns]

In [152]:
df_merge['Date'] = pd.to_datetime(df_merge['Date'])
df_merge=df_merge.dropna()

In [153]:
df_merge.Index.unique()

array(['NYA', 'IXIC', 'HSI', '000001.SS', 'GSPTSE', '399001.SZ', 'NSEI',
       'GDAXI', 'KS11', 'SSMI', 'TWII', 'J203.JO', 'N225', 'N100'],
      dtype=object)

In [154]:
options = ["NYA", "NASDAQ", "HSI", "N100", "SSMI"]
df_usa_eur = df_merge[df_merge["Index"].isin(options)]
df_usa_eur.head()

Index       Date        Open        High         Low       Close  \
0   NYA 1965-12-31  528.690002  528.690002  528.690002  528.690002   
1   NYA 1966-01-03  527.210022  527.210022  527.210022  527.210022   
2   NYA 1966-01-04  527.840027  527.840027  527.840027  527.840027   
3   NYA 1966-01-05  531.119995  531.119995  531.119995  531.119995   
4   NYA 1966-01-06  532.070007  532.070007  532.070007  532.070007   

    Adj Close  Volume         Region                 Exchange Currency  
0  528.690002     0.0  United States  New York Stock Exchange      USD  
1  527.210022     0.0  United States  New York Stock Exchange      USD  
2  527.840027     0.0  United States  New York Stock Exchange      USD  
3  531.119995     0.0  United States  New York Stock Exchange      USD  
4  532.070007     0.0  United States  New York Stock Exchange      USD

In [155]:
fig = px.line(df_usa_eur, x='Date', y="Volume", color = "Region", 
             labels = {"Index":"Region"}, color_discrete_map={
             })
# Add figure title
fig.update_layout(
    plot_bgcolor = "white",
    title_text="Volume traded in USA and Europe Exchanges"
)

fig.update_yaxes(showticklabels = True, showline = True, linewidth = 2, linecolor = "black")
fig.update_xaxes(showticklabels = True, showline = True, linewidth = 2, linecolor = "black")

iplot(fig)

### Volatilité des marchés boursiers

In [156]:
options2 = ["HSI", "N100", "SSMI"]
df_eur = df_merge[df_merge["Index"].isin(options2)]
df_eur.head()

Index       Date         Open         High          Low        Close  \
26638   HSI 1986-12-31  2568.300049  2568.300049  2568.300049  2568.300049   
26640   HSI 1987-01-02  2540.100098  2540.100098  2540.100098  2540.100098   
26641   HSI 1987-01-05  2552.399902  2552.399902  2552.399902  2552.399902   
26642   HSI 1987-01-06  2583.899902  2583.899902  2583.899902  2583.899902   
26643   HSI 1987-01-07  2607.100098  2607.100098  2607.100098  2607.100098   

         Adj Close  Volume     Region                  Exchange Currency  
26638  2568.300049     0.0  Hong Kong  Hong Kong Stock Exchange      HKD  
26640  2540.100098     0.0  Hong Kong  Hong Kong Stock Exchange      HKD  
26641  2552.399902     0.0  Hong Kong  Hong Kong Stock Exchange      HKD  
26642  2583.899902     0.0  Hong Kong  Hong Kong Stock Exchange      HKD  
26643  2607.100098     0.0  Hong Kong  Hong Kong Stock Exchange      HKD

In [157]:
df_eur["Return"] = (df_eur["Close"]/df_eur["Close"].shift(1)) - 1

<ipython-input-157-7d970161de24>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [158]:
fig = px.histogram(df_eur, x = "Return", color = "Region",color_discrete_map={
             })

fig.update_layout(
    plot_bgcolor = "white",
    title_text="Stock Volatility of USA and Europe Exchanges"
)

## Séparation des données boursières

In [159]:
index = data.groupby(data.Index)        
HSI = index.get_group("HSI")         # hongkong Stock Exchange

In [160]:
HSI

Index          Open          High           Low         Close  \
Date                                                                       
1986-12-31   HSI   2568.300049   2568.300049   2568.300049   2568.300049   
1987-01-02   HSI   2540.100098   2540.100098   2540.100098   2540.100098   
1987-01-05   HSI   2552.399902   2552.399902   2552.399902   2552.399902   
1987-01-06   HSI   2583.899902   2583.899902   2583.899902   2583.899902   
1987-01-07   HSI   2607.100098   2607.100098   2607.100098   2607.100098   
...          ...           ...           ...           ...           ...   
2021-05-25   HSI  28461.500000  28929.240230  28461.500000  28910.859380   
2021-05-26   HSI  29056.279300  29261.859380  29027.949220  29166.009770   
2021-05-27   HSI  28998.390630  29157.949220  28950.720700  29113.199220   
2021-05-28   HSI  29219.460940  29336.130860  29033.720700  29124.410160   
2021-05-31   HSI  29225.460940  29225.460940  28909.519530  29151.800780   

               Adj Close        Volume  
Date                                    
1986-12-31   2568.300049  0.000000e+00  
1987-01-02   2540.100098  0.000000e+00  
1987-01-05   2552.399902  0.000000e+00  
1987-01-06   2583.899902  0.000000e+00  
1987-01-07   2607.100098  0.000000e+00  
...                  ...           ...  
2021-05-25  28910.859380  2.352078e+09  
2021-05-26  29166.009770  2.518538e+09  
2021-05-27  29113.199220  3.804955e+09  
2021-05-28  29124.410160  2.591560e+09  
2021-05-31  29151.800780  2.188581e+09  

[8492 rows x 7 columns]

In [161]:
data_hongkong = HSI.filter(['Close'])
dataset_hongkong = data_hongkong.values  # total data NYA stock market 
training_data_hongkong_len = math.ceil(len(dataset_hongkong) * .8) # take 80% of the total data for training so the rest 20% will be for testing
testing_data_hongkong_len = dataset_hongkong[training_data_hongkong_len:]  # takes 20% of data for testing
testing_data_hongkong_len.shape


(1698, 1)

In [162]:
data_hongkong.tail(5)

Close
Date                   
2021-05-25  28910.85938
2021-05-26  29166.00977
2021-05-27  29113.19922
2021-05-28  29124.41016
2021-05-31  29151.80078

In [163]:
data_hongkong.shape

(8492, 1)

## Analyse de la structure de nos données

In [164]:
print(testing_data_hongkong_len)
testing_data_hongkong_len.shape

[[23238.99023]
 [23233.44922]
 [23346.66992]
 ...
 [29113.19922]
 [29124.41016]
 [29151.80078]]


(1698, 1)

In [165]:
data_hongkong.shape
data_hongkong

Close
Date                    
1986-12-31   2568.300049
1987-01-02   2540.100098
1987-01-05   2552.399902
1987-01-06   2583.899902
1987-01-07   2607.100098
...                  ...
2021-05-25  28910.859380
2021-05-26  29166.009770
2021-05-27  29113.199220
2021-05-28  29124.410160
2021-05-31  29151.800780

[8492 rows x 1 columns]

## Affichage de nos données avec des graphiques

In [166]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = HSI.index, y = HSI.High,
                    mode='lines',
                    name='High',
                    marker_color = '#2CA02C',
                    visible = "legendonly"))
fig.add_trace(go.Scatter(x = HSI.index, y = HSI.Low,
                    mode='lines',
                    name='Low',
                    marker_color = '#D62728',
                    visible = "legendonly"))
fig.add_trace(go.Scatter(x = HSI.index, y = HSI.Open,
                    mode='lines',
                    name='Open',
                    marker_color = '#FF7F0E',
                    visible = "legendonly"))
fig.add_trace(go.Scatter(x = HSI.index, y = HSI.Close,
                    mode='lines',
                    name='Close',
                    marker_color = '#1F77B4'))

fig.update_layout(
    title='Price history of Hong Kong Stock Exchange',
    titlefont_size = 26,
    
    xaxis = dict(
        title='Year',
        titlefont_size=16,
        tickfont_size=14),
    
    height = 800,
    
    yaxis=dict(
        title='Price in CAD (CA$)',
        titlefont_size=16,
        tickfont_size=14),
    
    legend=dict(
        y=0,
        x=1.0,
        bgcolor='rgba(255, 255, 255, 0)',
        bordercolor='rgba(255, 255, 255, 0)'))

fig.show()

## Normalisation de nos données avec MinMaxScaler

In [167]:
scaler_hongkong = MinMaxScaler(feature_range=(0,1))
scaled_data_hongkong = scaler_hongkong.fit_transform(dataset_hongkong)


In [168]:
scaled_data_hongkong

array([[0.02154244],
       [0.02064031],
       [0.02103379],
       ...,
       [0.87072864],
       [0.87108729],
       [0.87196353]])

In [169]:
print(dataset_hongkong.shape,  scaled_data_hongkong.shape)
scaled_data_hongkong[0:5, :]

(8492, 1) (8492, 1)


array([[0.02154244],
       [0.02064031],
       [0.02103379],
       [0.02204149],
       [0.02278368]])

In [170]:
dataset_hongkong, scaled_data_hongkong

(array([[ 2568.300049],
        [ 2540.100098],
        [ 2552.399902],
        ...,
        [29113.19922 ],
        [29124.41016 ],
        [29151.80078 ]]),
 array([[0.02154244],
        [0.02064031],
        [0.02103379],
        ...,
        [0.87072864],
        [0.87108729],
        [0.87196353]]))

In [171]:
train_data_hongkong = scaled_data_hongkong[0:training_data_hongkong_len, :]


### Declaration de nos données d'entrainement

In [172]:
x_train_hongkong = []
y_train_hongkong = []


In [173]:
print(train_data_hongkong.shape)
print(train_data_hongkong[0:1,0])
print(train_data_hongkong[60,0])
print(scaled_data_hongkong.shape)
print(train_data_hongkong[0:60, 0])
print(train_data_hongkong[60, 0])
print(range(60, len(train_data_hongkong)))


(6794, 1)
[0.02154244]
0.028151689261289928
(8492, 1)
[0.02154244 0.02064031 0.02103379 0.02204149 0.02278368 0.02266211
 0.0213313  0.0230332  0.02226223 0.02185915 0.02124813 0.02072029
 0.01809386 0.01775476 0.02044196 0.02053794 0.01933829 0.01885843
 0.02012526 0.02106259 0.02208308 0.02276128 0.0237274  0.02487266
 0.02491105 0.02619387 0.02559244 0.02701923 0.02750548 0.02705122
 0.02787018 0.02870193 0.02900264 0.02818049 0.02983119 0.03148191
 0.0304966  0.03130916 0.03034945 0.03144672 0.03197137 0.03340455
 0.03186259 0.02890347 0.02890987 0.02960726 0.02675051 0.02770382
 0.02735833 0.0264338  0.02478309 0.02349387 0.02652337 0.026437
 0.02833404 0.02938333 0.02985359 0.02996236 0.02841402 0.02891307]
0.028151689261289928
range(60, 6794)


In [174]:
for i in range(60, len(train_data_hongkong)):
    x_train_hongkong.append(train_data_hongkong[i-60:i, 0])
    y_train_hongkong.append(train_data_hongkong[i, 0])

### Données d'entrainement pour la prédictions boursières pour Hong Kong. Conversion de nos données d'entrainement en np arrays


In [175]:
x_train_hongkong, y_train_hongkong = np.array(x_train_hongkong), np.array(y_train_hongkong)
x_train_hongkong = np.reshape(x_train_hongkong, (x_train_hongkong.shape[0], x_train_hongkong.shape[1],1))
x_train_hongkong.shape

(6734, 60, 1)

### Definition du modèle

In [176]:
def modelo(x_train, y_train):
    model = Sequential()
    model.add(LSTM(50, return_sequences = True, input_shape = (x_train.shape[1], 1)))
    model.add(Dropout(0.2))
    model.add(LSTM(50, return_sequences = False))
    model.add(Dense(25, activation="relu"))
    model.add(Dense(1))
    model.compile(optimizer = 'adam', loss = 'mean_squared_error')
    model.fit(x_train, y_train, batch_size = 1, epochs = 3)
    return model

## Train model pour Hong Kong

In [177]:
import time

In [178]:
modelo_hongkong = modelo(x_train_hongkong, y_train_hongkong)

Epoch 1/3
6734/6734 [==============================] - 110s 16ms/step - loss: 0.0012
Epoch 2/3
6734/6734 [==============================] - 102s 15ms/step - loss: 3.8221e-04
Epoch 3/3
6734/6734 [==============================] - 101s 15ms/step - loss: 2.8759e-04


In [179]:
modelo_hongkong.summary()
modelo_hongkong.save('hongkong_stock_prediction_model.h5')

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_6 (LSTM)                (None, 60, 50)            10400     
_________________________________________________________________
dropout_3 (Dropout)          (None, 60, 50)            0         
_________________________________________________________________
lstm_7 (LSTM)                (None, 50)                20200     
_________________________________________________________________
dense_6 (Dense)              (None, 25)                1275      
_________________________________________________________________
dense_7 (Dense)              (None, 1)                 26        
Total params: 31,901
Trainable params: 31,901
Non-trainable params: 0
_________________________________________________________________


### Pour notre phase de test nous utilisions 20% du dataset

In [180]:
test_data_hongkong = scaled_data_hongkong[training_data_hongkong_len-60:, :]
x_test_hongkong = []

***Use 60 Window to generate x_test_nya***

In [181]:
for i in range (60, len(test_data_hongkong)):
    x_test_hongkong.append(test_data_hongkong[i - 60:i, 0])

### Nous convertissons les données de test en array et nous changons leurs tailles

In [182]:
x_test_hongkong = np.array(x_test_hongkong)
x_test_hongkong = np.reshape(x_test_hongkong, (x_test_hongkong.shape[0], x_test_hongkong.shape[1], 1))

y_test_hongkong = dataset_hongkong[training_data_hongkong_len:, :]
#y_test_hongkong = scaler_hongkong.fit_transform(y_test_hongkong)

## Prediction de notre modèle

In [183]:
predictions_hongkong = modelo_hongkong.predict(x_test_hongkong)

In [184]:
print("Prediction ", predictions_hongkong)
print("Label ", y_test_hongkong)
rsme_hongkong = np.sqrt(np.mean(predictions_hongkong - y_test_hongkong) ** 2)
print(predictions_hongkong.shape)

Prediction  [[0.69787306]
 [0.6953591 ]
 [0.6944615 ]
 ...
 [0.8647686 ]
 [0.8691362 ]
 [0.87057465]]
Label  [[23238.99023]
 [23233.44922]
 [23346.66992]
 ...
 [29113.19922]
 [29124.41016]
 [29151.80078]]
(1698, 1)


### Etude de la prédiction

In [185]:
predictions_hongkong

array([[0.69787306],
       [0.6953591 ],
       [0.6944615 ],
       ...,
       [0.8647686 ],
       [0.8691362 ],
       [0.87057465]], dtype=float32)

In [186]:
predictions_hongkong = scaler_hongkong.inverse_transform(predictions_hongkong)
train_hongkong = data_hongkong[:training_data_hongkong_len]
valid_hongkong = data_hongkong[training_data_hongkong_len:]
valid_hongkong['Predictions'] = predictions_hongkong


<ipython-input-186-4800e4fa4e41>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [187]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = train_hongkong.index, y = train_hongkong.Close,
                    mode='lines',
                    name='Close',
                    marker_color = '#1F77B4'))
fig.add_trace(go.Scatter(x = valid_hongkong.index, y = valid_hongkong.Close,
                    mode='lines',
                    name='Val',
                    marker_color = '#FF7F0E'))
fig.add_trace(go.Scatter(x = valid_hongkong.index, y = valid_hongkong.Predictions,
                    mode='lines',
                    name='Predictions',
                    marker_color = '#2CA02C'))

fig.update_layout(
    title='Hong Kong Stock Exchange Price Predictions',
    titlefont_size = 28,
    hovermode = 'x',
    xaxis = dict(
        title='Date',
        titlefont_size=16,
        tickfont_size=14),
    
    height = 800,
    
    yaxis=dict(
        title='Close price in USD (US$)',
        titlefont_size=16,
        tickfont_size=14),
    legend=dict(
        y=0,
        x=1.0,
        bgcolor='rgba(255, 255, 255, 0)',
        bordercolor='rgba(255, 255, 255, 0)'))

fig.show()

### Calcul de la RMSE

In [188]:
y_test_hongkong = scaler_hongkong.fit_transform(y_test_hongkong)
predictions_hongkong = scaler_hongkong.fit_transform(predictions_hongkong)

In [189]:
from statsmodels.tools.eval_measures import rmse
error=rmse(predictions_hongkong, y_test_hongkong)
error

array([0.03491293])